# Pytket to QIR

pytket-qir is an client-side extension (plugin) for pytket, the quantum circuit toolkit & compiler framework by Quantinuum. Its purpose is to provide functionality for 1-way conversion of pytket circuits into the QIR (Quantum Intermediate Representation) format. It allows users of pytket to target QIR-compliant hardware providers or off-the-shelf simulation tool. 

pytket-qir is cross-platform on Windows, Linux and macOS. It is compatible with Python 3.10 - 3.13, and available on PyPi. An API reference is available at [https://docs.quantinuum.com/tket/extensions/pytket-qir/](https://docs.quantinuum.com/tket/extensions/pytket-qir/). The package is opensource (Apache 2.0), available at [https://github.com/CQCL/pytket-qir.git](https://github.com/CQCL/pytket-qir.git), and downloadable via PyPI.

```{code} bash
pip install pytket-qir
```

## Basic Usage

In [1]:
from pytket.circuit import Circuit, Qubit
from pytket.circuit.clexpr import wired_clexpr_from_logic_exp

circ = Circuit(3)
a = circ.add_c_register("a", 5)
b = circ.add_c_register("b", 5)
c = circ.add_c_register("c", 5)
d = circ.add_c_register("d", 5)
circ.H(0)
circ.add_clexpr(*wired_clexpr_from_logic_exp(a | b, c))  # type: ignore
circ.add_clexpr(*wired_clexpr_from_logic_exp(c | b, d))  # type: ignore
circ.add_clexpr(*wired_clexpr_from_logic_exp(c | b, d), condition=a[4])  # type: ignore
circ.H(0)
circ.Measure(Qubit(0), d[4])
circ.H(1)
circ.Measure(Qubit(1), d[3])
circ.H(2)
circ.Measure(Qubit(2), d[2])

[ClExpr a[0], a[1], a[2], a[3], a[4], b[0], b[1], b[2], b[3], b[4], c[0], c[1], c[2], c[3], c[4]; H q[0]; H q[1]; H q[2]; ClExpr c[0], c[1], c[2], c[3], c[4], b[0], b[1], b[2], b[3], b[4], d[0], d[1], d[2], d[3], d[4]; H q[0]; IF ([a[4]] == 1) THEN ClExpr c[0], c[1], c[2], c[3], c[4], b[0], b[1], b[2], b[3], b[4], d[0], d[1], d[2], d[3], d[4]; Measure q[2] --> d[2]; Measure q[1] --> d[3]; Measure q[0] --> d[4]; ]

In [2]:
from pytket.qir.conversion.api import QIRFormat, QIRProfile, pytket_to_qir


gen_qir_ll = pytket_to_qir(
    circ,
    name="conditional",
    qir_format=QIRFormat.STRING,
    profile=QIRProfile.ADAPTIVE,
    cut_pytket_register=True,
)

print(gen_qir_ll)

; ModuleID = 'conditional'
source_filename = "conditional"

%Qubit = type opaque
%Result = type opaque

@0 = internal constant [2 x i8] c"a\00"
@1 = internal constant [2 x i8] c"b\00"
@2 = internal constant [2 x i8] c"c\00"
@3 = internal constant [2 x i8] c"d\00"

define void @main() #0 {
entry:
  call void @__quantum__qis__h__body(%Qubit* null)
  call void @__quantum__qis__h__body(%Qubit* inttoptr (i64 1 to %Qubit*))
  call void @__quantum__qis__h__body(%Qubit* inttoptr (i64 2 to %Qubit*))
  call void @__quantum__qis__h__body(%Qubit* null)
  br i1 false, label %condb0, label %contb0

condb0:                                           ; preds = %entry
  br label %contb0

contb0:                                           ; preds = %condb0, %entry
  %0 = phi i64 [ 0, %condb0 ], [ 0, %entry ]
  call void @__quantum__qis__mz__body(%Qubit* inttoptr (i64 2 to %Qubit*), %Result* inttoptr (i64 2 to %Result*))
  %1 = call i1 @__quantum__qis__read_result__body(%Result* inttoptr (i64 2 to %Result*

## Use Cases

### Wasm Callouts

In [3]:
from pytket import wasm
from pytket.circuit import Bit, Circuit, Qubit
from pytket.wasm import WasmFileHandler

w = WasmFileHandler("testfile.wasm")
c = Circuit(6, 6)
c0 = c.add_c_register("c0", 3)
c1 = c.add_c_register("c1", 4)
c2 = c.add_c_register("c2", 5)
c.add_wasm_to_reg("multi", w, [c0, c1], [c2])
c.add_wasm_to_reg("add_one", w, [c2], [c2])
c.add_wasm_to_reg("no_return", w, [c2], [])
c.add_wasm_to_reg("init", w, [], [])
c.add_wasm_to_reg("no_parameters", w, [], [c2])

ValueError: wasm file not found at given path

In [ ]:
from pytket.qir.conversion.api import QIRFormat, QIRProfile, pytket_to_qir

profile = QIRProfile.ADAPTIVE

result = pytket_to_qir(
    c,
    name=f"pytket_qir_wasm_2-{profile}",
    qir_format=QIRFormat.STRING,
    int_type=32,
    profile=profile,
)

AttributeError: 'pytket._tket.unit_id.BitRegister' object has no attribute 'q_registers'

### RNG Callouts

In [4]:
circ = Circuit()
creg = circ.add_c_register("c", 64)
circ.add_c_setbits([True, True], [creg[3], creg[11]])
circ.set_rng_seed(creg)

[SetBits(11) c[3], c[11]; RNGSeed c[0], c[1], c[2], c[3], c[4], c[5], c[6], c[7], c[8], c[9], c[10], c[11], c[12], c[13], c[14], c[15], c[16], c[17], c[18], c[19], c[20], c[21], c[22], c[23], c[24], c[25], c[26], c[27], c[28], c[29], c[30], c[31], c[32], c[33], c[34], c[35], c[36], c[37], c[38], c[39], c[40], c[41], c[42], c[43], c[44], c[45], c[46], c[47], c[48], c[49], c[50], c[51], c[52], c[53], c[54], c[55], c[56], c[57], c[58], c[59], c[60], c[61], c[62], c[63], _r[0]; ]

In [5]:
from pytket.qir.conversion.api import QIRFormat, QIRProfile, pytket_to_qir

profile = QIRProfile.ADAPTIVE

result = pytket_to_qir(
    circ,
    name=f"pytket_rng_wasm-{profile}",
    qir_format=QIRFormat.STRING,
    int_type=64,
    profile=profile,
    cut_pytket_register=True
)